In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list the files in the input directory

import os
print(os.listdir("../input"))

# Any results you write to the current directory are saved as output.

['user.csv', 'item.csv', 'data.csv']


In [1]:
import numpy as np
import pandas as pd
from sklearn import preprocessing
from sklearn.impute import SimpleImputer

In [2]:
datasetData=pd.read_csv('data.csv')

In [3]:
datasetItem=pd.read_csv('item.csv')

In [4]:
datasetUser=pd.read_csv('user.csv')


In [5]:
X=datasetData.iloc[:,:]
X=np.array(X)
recommendMatrix=np.zeros((943,1682))
for dataPoint in range(100000):
    recommendMatrix[X[dataPoint][0]-1][X[dataPoint][1]-1]=X[dataPoint][2]

In [6]:
X=[[] for data in range(100000)]

In [7]:
y=[[] for data in range(100000)]

In [8]:
y=datasetData.iloc[:,2]

In [9]:
y=np.array(y)

In [10]:
XData=np.array(datasetData.iloc[:,:-1])
XUser=np.array(datasetUser.iloc[:])
XItem=np.array(datasetItem.iloc[:])
XUser[:,3]=preprocessing.OrdinalEncoder().fit_transform(XUser[:,3].reshape(-1,1)).reshape(943)
XItem=SimpleImputer(strategy='constant').fit_transform(XItem)

In [11]:
X=np.zeros((100000,23))

In [12]:
for i in range(100000):
        dataPoint=[]
        #user info:
        user=XData[i][0]-1;
        for userInfo in range(4):
            #dataPoint.append(int(XUser[user][userInfo]))
            X[i][userInfo]=int(XUser[user][userInfo])
        #movie info
        movie=XData[i][1]-1
        for movieInfo in range(19):
            #dataPoint.append(int(XItem[movie][movieInfo]))
            X[i][4+movieInfo]=int(XItem[movie][movieInfo])
        
        

In [13]:
X.shape

(100000, 23)

In [14]:
X

array([[49.,  1., 21., ...,  0.,  0.,  0.],
       [39.,  2.,  7., ...,  1.,  0.,  0.],
       [25.,  1., 21., ...,  0.,  0.,  0.],
       ...,
       [21.,  1., 19., ...,  1.,  0.,  0.],
       [47.,  1.,  4., ...,  0.,  0.,  0.],
       [28.,  2., 14., ...,  0.,  0.,  1.]])

In [15]:
import time
numberOfwhale=3
iterations=3

dataPoints = X.shape[0]
features=X.shape[1];
learningRate=0.0001
startTimeAlgo=time.time()
bestWhale=0
#initialize features
WFC1=np.random.uniform(low=0,high=1,size=(numberOfwhale,features,100))
WC1=np.random.uniform(low=0,high=1,size=(numberOfwhale,5,3,3))
WC2=np.random.uniform(low=0,high=1,size=(numberOfwhale,5,3,3))
WFC2=np.random.uniform(low=0,high=0.001,size=(numberOfwhale,36,84))
WFC3=np.random.uniform(low=0,high=0.0001,size=(numberOfwhale,84,10))
WOP=np.random.uniform(low=0,high=1,size=(numberOfwhale,10))

#Application of WOA

centresOfwhale=[[] for whale in range(numberOfwhale)]
fitness=np.zeros((numberOfwhale))
for whale in range(numberOfwhale):
    for nodeI1 in range(features):
        for nodeF1 in range(100):
            centresOfwhale[whale].append(WFC1[whale][nodeI1][nodeF1])
    
    for kernel in range(5):
        for rowKernel in range(3):
            for colKernel in range(3):
                centresOfwhale[whale].append(WC1[whale][kernel][rowKernel][colKernel])
    
    for depthKernel in range(5):
        for rowKernel in range(3):
            for colKernel in range(3):
                centresOfwhale[whale].append(WC2[whale][depthKernel][rowKernel][colKernel])
    
    for nodeC2 in range(36):
        for nodeF2 in range(84):
            centresOfwhale[whale].append(WFC2[whale][nodeC2][nodeF2])
    
    for nodeF2 in range(84):
        for nodeF3 in range(10):
            centresOfwhale[whale].append(WFC3[whale][nodeF2][nodeF3])
    
    for node in range(10):
        centresOfwhale[whale].append(WOP[whale][node])

centresOfwhale=np.array(centresOfwhale)
features1=centresOfwhale.shape[1]

In [17]:
import math
import random
for iteration in range(iterations):
    print("iteration "+str(iteration))
    fitness=np.zeros((numberOfwhale))
    bestWhale=0
    bestAccuracy=-100
    startTime=time.time();
    for whale in range(numberOfwhale):
        accuracy=0.00
        print("whale: "+str(whale))
        #apply cnn
        for dataPoint in range(10000):
            #initializations
            print("iteration "+str(iteration))
            print("whale: "+str(whale))
            print(dataPoint)
            #startTime=time.time()
            I1=np.zeros((features))
            sigmaF1=np.zeros((100))
            sigmaC1=np.zeros((5,8,8))
            sigmaC2=np.zeros((6,6))
            sigmaF2=np.zeros((84))
            sigmaF3=np.zeros((10))
            
            I1=X[dataPoint]
            
            #Forward passs at I1
            for nodeI1 in range(features):
                for nodeF1 in range(100):
                    sigmaF1[nodeF1]+=WFC1[whale][nodeI1][nodeF1]*I1[nodeI1]
            
            F1=sigmaF1
            for nodeF1 in range(100):
                if sigmaF1[nodeF1]<0:
                    F1[nodeF1]*=0.05
            sigmaF1=sigmaF1.reshape((10,10))
            F1=F1.reshape((10,10))
            #Forward Pass at I1 done
            
            #Forward pass at F1
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                sigmaC1[kernel][rowC1][colC1]+=WC1[whale][kernel][rowKernel][colKernel]*F1[rowC1+rowKernel][colC1+colKernel]
            
            C1=sigmaC1
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        if C1[kernel][rowC1][colC1]<0:
                            C1[kernel][rowC1][colC1]*=0.05
            #Forward pass at F1 done
            
            #Forward pass at C1
            for rowC2 in range(6):
                for colC2 in range(6):
                    for depthKernel in range(5):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                sigmaC2[rowC2][colC2]+=WC2[whale][depthKernel][rowKernel][colKernel]*C1[depthKernel][rowKernel+rowC2][colKernel+colC2]
            
            C2=sigmaC2
            for rowC2 in range(6):
                for colC2 in range(6):
                    if sigmaC2[rowC2][colC2]<0:
                        C2[rowC2][colC2]*=0.05
            
            sigmaC2=sigmaC2.reshape((36,1))
            C2=C2.reshape((36,1))
            #Forward pass at C1 done
            
            #Forward pass at C2
            for nodeC2 in range(36):
                for nodeF2 in range(84):
                    sigmaF2[nodeF2]+=WFC2[whale][nodeC2][nodeF2]*C2[nodeC2]
            
            F2=sigmaF2
            for nodeF2 in range(84):
                if F2[nodeF2]<0:
                    F2[nodeF2]*=0.05
            #Forward pass at C2 done
            
            #Forward pass at F2
            for nodeF2 in range(84):
                for nodeF3 in range(10):
                    sigmaF3[nodeF3]+=WFC3[whale][nodeF2][nodeF3]*F2[nodeF3]
                    
            F3=sigmaF3
            for nodeF3 in range(10):
                if F3[nodeF3]<0:
                    F3[nodeF3]*=0.05
            #Forward pass at F2 done
            
            #Forward pass at F3
            sum=0.00
            for node in range(10):
                sum+=F3[node]*WOP[whale][node]
            
            op=sum
            accuracy+=(math.pow(op-y[dataPoint],2))
         
        accuracy=math.sqrt(accuracy)
        fitness[whale]=accuracy
        if accuracy>bestAccuracy:
            bestAccuracy=accuracy
            bestWhale=whale
        
    print("cnn applied")
    print(time.time()-startTime)
    startTime=time.time()
    
    #apply woaSa equations
    a=2-iteration*((2.00)/iterations) #eqn 2.3
    a2=-1+iteration*((-1.00)/iterations)
    for whale in range(numberOfwhale):
        print(whale)
        r1=random.random()
        r2=random.random()
        A=2*a*r1-a;  # Eq. (2.3) in the paper
        C=2*r2;      # Eq. (2.4) in the paper
        p=random.random()
        b=1;               #  parameters in Eq. (2.5)
        l=(a2-1)*random.random()+1;   #  parameters in Eq. (2.5)
        
        for cluster in range(features1):
            if p<0.5 :
                if abs(A)>=1 :
                    rand_leader_index = int(math.floor((numberOfwhale-1)*random.random()+1));
                    X_rand = centresOfwhale[rand_leader_index]
                    D_X_rand=abs(C*X_rand[cluster]-centresOfwhale[whale,cluster]); # Eq. (2.7)
                    centresOfwhale[whale,cluster]=X_rand[cluster]-A*D_X_rand*0.001;      # Eq. (2.8)
                elif abs(A)<1 :
                    D_Leader=abs(C*centresOfwhale[bestWhale,cluster]-centresOfwhale[whale,cluster]); # Eq. (2.1)
                    centresOfwhale[whale,cluster]=centresOfwhale[bestWhale,cluster]-A*D_Leader*0.001;      # Eq. (2.2)
            elif p>=0.5 :
                distance2Leader=abs(centresOfwhale[bestWhale,cluster]-centresOfwhale[whale,cluster]);      # Eq. (2.5)
                centresOfwhale[whale,cluster]=distance2Leader*math.exp(b*l)*math.cos(l*2*3.14)*0.001+centresOfwhale[whale,cluster];
        
    print("WOA applied")
    print(time.time()-startTime)



    
    for whale in range(numberOfwhale):
        cnt=0
        for nodeI1 in range(features):
            for nodeF1 in range(100):
                WFC1[whale][nodeI1][nodeF1]=centresOfwhale[whale][cnt]
                cnt+=1
        
        for kernel in range(5):
            for rowKernel in range(3):
                for colKernel in range(3):
                    WC1[whale][kernel][rowKernel][colKernel]=centresOfwhale[whale][cnt]
                    cnt+=1
        
        for depthKernel in range(5):
            for rowKernel in range(3):
                for colKernel in range(3):
                    WC2[whale][depthKernel][rowKernel][colKernel]=centresOfwhale[whale][cnt]
                    cnt+=1
        
        for nodeC2 in range(36):
            for nodeF2 in range(84):
                WFC2[whale][nodeC2][nodeF2]=centresOfwhale[whale][cnt]
                cnt+=1
        
        for nodeF2 in range(84):
            for nodeF3 in range(10):
                WFC3[whale][nodeF2][nodeF3]=centresOfwhale[whale][cnt]
                cnt+=1
        
        for node in range(10):
            WOP[whale][node]=centresOfwhale[whale][cnt]
            cnt+=1


iteration 0
whale: 0
iteration 0
whale: 0
0
iteration 0
whale: 0
1
iteration 0
whale: 0
2
iteration 0
whale: 0
3
iteration 0
whale: 0
4
iteration 0
whale: 0
5
iteration 0
whale: 0
6
iteration 0
whale: 0
7
iteration 0
whale: 0
8
iteration 0
whale: 0
9
iteration 0
whale: 0
10
iteration 0
whale: 0
11
iteration 0
whale: 0
12
iteration 0
whale: 0
13
iteration 0
whale: 0
14
iteration 0
whale: 0
15
iteration 0
whale: 0
16
iteration 0
whale: 0
17
iteration 0
whale: 0
18
iteration 0
whale: 0
19
iteration 0
whale: 0
20
iteration 0
whale: 0
21
iteration 0
whale: 0
22
iteration 0
whale: 0
23
iteration 0
whale: 0
24
iteration 0
whale: 0
25
iteration 0
whale: 0
26
iteration 0
whale: 0
27
iteration 0
whale: 0
28
iteration 0
whale: 0
29
iteration 0
whale: 0
30
iteration 0
whale: 0
31
iteration 0
whale: 0
32
iteration 0
whale: 0
33
iteration 0
whale: 0
34
iteration 0
whale: 0
35
iteration 0
whale: 0
36
iteration 0
whale: 0
37
iteration 0
whale: 0
38
iteration 0
whale: 0
39
iteration 0
whale: 0
40
itera

iteration 0
whale: 0
342
iteration 0
whale: 0
343
iteration 0
whale: 0
344
iteration 0
whale: 0
345
iteration 0
whale: 0
346
iteration 0
whale: 0
347
iteration 0
whale: 0
348
iteration 0
whale: 0
349
iteration 0
whale: 0
350
iteration 0
whale: 0
351
iteration 0
whale: 0
352
iteration 0
whale: 0
353
iteration 0
whale: 0
354
iteration 0
whale: 0
355
iteration 0
whale: 0
356
iteration 0
whale: 0
357
iteration 0
whale: 0
358
iteration 0
whale: 0
359
iteration 0
whale: 0
360
iteration 0
whale: 0
361
iteration 0
whale: 0
362
iteration 0
whale: 0
363
iteration 0
whale: 0
364
iteration 0
whale: 0
365
iteration 0
whale: 0
366
iteration 0
whale: 0
367
iteration 0
whale: 0
368
iteration 0
whale: 0
369
iteration 0
whale: 0
370
iteration 0
whale: 0
371
iteration 0
whale: 0
372
iteration 0
whale: 0
373
iteration 0
whale: 0
374
iteration 0
whale: 0
375
iteration 0
whale: 0
376
iteration 0
whale: 0
377
iteration 0
whale: 0
378
iteration 0
whale: 0
379
iteration 0
whale: 0
380
iteration 0
whale: 0
381


iteration 0
whale: 0
678
iteration 0
whale: 0
679
iteration 0
whale: 0
680
iteration 0
whale: 0
681
iteration 0
whale: 0
682
iteration 0
whale: 0
683
iteration 0
whale: 0
684
iteration 0
whale: 0
685
iteration 0
whale: 0
686
iteration 0
whale: 0
687
iteration 0
whale: 0
688
iteration 0
whale: 0
689
iteration 0
whale: 0
690
iteration 0
whale: 0
691
iteration 0
whale: 0
692
iteration 0
whale: 0
693
iteration 0
whale: 0
694
iteration 0
whale: 0
695
iteration 0
whale: 0
696
iteration 0
whale: 0
697
iteration 0
whale: 0
698
iteration 0
whale: 0
699
iteration 0
whale: 0
700
iteration 0
whale: 0
701
iteration 0
whale: 0
702
iteration 0
whale: 0
703
iteration 0
whale: 0
704
iteration 0
whale: 0
705
iteration 0
whale: 0
706
iteration 0
whale: 0
707
iteration 0
whale: 0
708
iteration 0
whale: 0
709
iteration 0
whale: 0
710
iteration 0
whale: 0
711
iteration 0
whale: 0
712
iteration 0
whale: 0
713
iteration 0
whale: 0
714
iteration 0
whale: 0
715
iteration 0
whale: 0
716
iteration 0
whale: 0
717


iteration 0
whale: 0
1014
iteration 0
whale: 0
1015
iteration 0
whale: 0
1016
iteration 0
whale: 0
1017
iteration 0
whale: 0
1018
iteration 0
whale: 0
1019
iteration 0
whale: 0
1020
iteration 0
whale: 0
1021
iteration 0
whale: 0
1022
iteration 0
whale: 0
1023
iteration 0
whale: 0
1024
iteration 0
whale: 0
1025
iteration 0
whale: 0
1026
iteration 0
whale: 0
1027
iteration 0
whale: 0
1028
iteration 0
whale: 0
1029
iteration 0
whale: 0
1030
iteration 0
whale: 0
1031
iteration 0
whale: 0
1032
iteration 0
whale: 0
1033
iteration 0
whale: 0
1034
iteration 0
whale: 0
1035
iteration 0
whale: 0
1036
iteration 0
whale: 0
1037
iteration 0
whale: 0
1038
iteration 0
whale: 0
1039
iteration 0
whale: 0
1040
iteration 0
whale: 0
1041
iteration 0
whale: 0
1042
iteration 0
whale: 0
1043
iteration 0
whale: 0
1044
iteration 0
whale: 0
1045
iteration 0
whale: 0
1046
iteration 0
whale: 0
1047
iteration 0
whale: 0
1048
iteration 0
whale: 0
1049
iteration 0
whale: 0
1050
iteration 0
whale: 0
1051
iteration 0


iteration 0
whale: 0
1333
iteration 0
whale: 0
1334
iteration 0
whale: 0
1335
iteration 0
whale: 0
1336
iteration 0
whale: 0
1337
iteration 0
whale: 0
1338
iteration 0
whale: 0
1339
iteration 0
whale: 0
1340
iteration 0
whale: 0
1341
iteration 0
whale: 0
1342
iteration 0
whale: 0
1343
iteration 0
whale: 0
1344
iteration 0
whale: 0
1345
iteration 0
whale: 0
1346
iteration 0
whale: 0
1347
iteration 0
whale: 0
1348
iteration 0
whale: 0
1349
iteration 0
whale: 0
1350
iteration 0
whale: 0
1351
iteration 0
whale: 0
1352
iteration 0
whale: 0
1353
iteration 0
whale: 0
1354
iteration 0
whale: 0
1355
iteration 0
whale: 0
1356
iteration 0
whale: 0
1357
iteration 0
whale: 0
1358
iteration 0
whale: 0
1359
iteration 0
whale: 0
1360
iteration 0
whale: 0
1361
iteration 0
whale: 0
1362
iteration 0
whale: 0
1363
iteration 0
whale: 0
1364
iteration 0
whale: 0
1365
iteration 0
whale: 0
1366
iteration 0
whale: 0
1367
iteration 0
whale: 0
1368
iteration 0
whale: 0
1369
iteration 0
whale: 0
1370
iteration 0


...

iteration 2
whale: 2
8571
iteration 2
whale: 2
8572
iteration 2
whale: 2
8573
iteration 2
whale: 2
8574
iteration 2
whale: 2
8575
iteration 2
whale: 2
8576
iteration 2
whale: 2
8577
iteration 2
whale: 2
8578
iteration 2
whale: 2
8579
iteration 2
whale: 2
8580
iteration 2
whale: 2
8581
iteration 2
whale: 2
8582
iteration 2
whale: 2
8583
iteration 2
whale: 2
8584
iteration 2
whale: 2
8585
iteration 2
whale: 2
8586
iteration 2
whale: 2
8587
iteration 2
whale: 2
8588
iteration 2
whale: 2
8589
iteration 2
whale: 2
8590
iteration 2
whale: 2
8591
iteration 2
whale: 2
8592
iteration 2
whale: 2
8593
iteration 2
whale: 2
8594
iteration 2
whale: 2
8595
iteration 2
whale: 2
8596
iteration 2
whale: 2
8597
iteration 2
whale: 2
8598
iteration 2
whale: 2
8599
iteration 2
whale: 2
8600
iteration 2
whale: 2
8601
iteration 2
whale: 2
8602
iteration 2
whale: 2
8603
iteration 2
whale: 2
8604
iteration 2
whale: 2
8605
iteration 2
whale: 2
8606
iteration 2
whale: 2
8607
iteration 2
whale: 2
8608
iteration 2


iteration 2
whale: 2
8892
iteration 2
whale: 2
8893
iteration 2
whale: 2
8894
iteration 2
whale: 2
8895
iteration 2
whale: 2
8896
iteration 2
whale: 2
8897
iteration 2
whale: 2
8898
iteration 2
whale: 2
8899
iteration 2
whale: 2
8900
iteration 2
whale: 2
8901
iteration 2
whale: 2
8902
iteration 2
whale: 2
8903
iteration 2
whale: 2
8904
iteration 2
whale: 2
8905
iteration 2
whale: 2
8906
iteration 2
whale: 2
8907
iteration 2
whale: 2
8908
iteration 2
whale: 2
8909
iteration 2
whale: 2
8910
iteration 2
whale: 2
8911
iteration 2
whale: 2
8912
iteration 2
whale: 2
8913
iteration 2
whale: 2
8914
iteration 2
whale: 2
8915
iteration 2
whale: 2
8916
iteration 2
whale: 2
8917
iteration 2
whale: 2
8918
iteration 2
whale: 2
8919
iteration 2
whale: 2
8920
iteration 2
whale: 2
8921
iteration 2
whale: 2
8922
iteration 2
whale: 2
8923
iteration 2
whale: 2
8924
iteration 2
whale: 2
8925
iteration 2
whale: 2
8926
iteration 2
whale: 2
8927
iteration 2
whale: 2
8928
iteration 2
whale: 2
8929
iteration 2


iteration 2
whale: 2
9216
iteration 2
whale: 2
9217
iteration 2
whale: 2
9218
iteration 2
whale: 2
9219
iteration 2
whale: 2
9220
iteration 2
whale: 2
9221
iteration 2
whale: 2
9222
iteration 2
whale: 2
9223
iteration 2
whale: 2
9224
iteration 2
whale: 2
9225
iteration 2
whale: 2
9226
iteration 2
whale: 2
9227
iteration 2
whale: 2
9228
iteration 2
whale: 2
9229
iteration 2
whale: 2
9230
iteration 2
whale: 2
9231
iteration 2
whale: 2
9232
iteration 2
whale: 2
9233
iteration 2
whale: 2
9234
iteration 2
whale: 2
9235
iteration 2
whale: 2
9236
iteration 2
whale: 2
9237
iteration 2
whale: 2
9238
iteration 2
whale: 2
9239
iteration 2
whale: 2
9240
iteration 2
whale: 2
9241
iteration 2
whale: 2
9242
iteration 2
whale: 2
9243
iteration 2
whale: 2
9244
iteration 2
whale: 2
9245
iteration 2
whale: 2
9246
iteration 2
whale: 2
9247
iteration 2
whale: 2
9248
iteration 2
whale: 2
9249
iteration 2
whale: 2
9250
iteration 2
whale: 2
9251
iteration 2
whale: 2
9252
iteration 2
whale: 2
9253
iteration 2


iteration 2
whale: 2
9535
iteration 2
whale: 2
9536
iteration 2
whale: 2
9537
iteration 2
whale: 2
9538
iteration 2
whale: 2
9539
iteration 2
whale: 2
9540
iteration 2
whale: 2
9541
iteration 2
whale: 2
9542
iteration 2
whale: 2
9543
iteration 2
whale: 2
9544
iteration 2
whale: 2
9545
iteration 2
whale: 2
9546
iteration 2
whale: 2
9547
iteration 2
whale: 2
9548
iteration 2
whale: 2
9549
iteration 2
whale: 2
9550
iteration 2
whale: 2
9551
iteration 2
whale: 2
9552
iteration 2
whale: 2
9553
iteration 2
whale: 2
9554
iteration 2
whale: 2
9555
iteration 2
whale: 2
9556
iteration 2
whale: 2
9557
iteration 2
whale: 2
9558
iteration 2
whale: 2
9559
iteration 2
whale: 2
9560
iteration 2
whale: 2
9561
iteration 2
whale: 2
9562
iteration 2
whale: 2
9563
iteration 2
whale: 2
9564
iteration 2
whale: 2
9565
iteration 2
whale: 2
9566
iteration 2
whale: 2
9567
iteration 2
whale: 2
9568
iteration 2
whale: 2
9569
iteration 2
whale: 2
9570
iteration 2
whale: 2
9571
iteration 2
whale: 2
9572
iteration 2


iteration 2
whale: 2
9857
iteration 2
whale: 2
9858
iteration 2
whale: 2
9859
iteration 2
whale: 2
9860
iteration 2
whale: 2
9861
iteration 2
whale: 2
9862
iteration 2
whale: 2
9863
iteration 2
whale: 2
9864
iteration 2
whale: 2
9865
iteration 2
whale: 2
9866
iteration 2
whale: 2
9867
iteration 2
whale: 2
9868
iteration 2
whale: 2
9869
iteration 2
whale: 2
9870
iteration 2
whale: 2
9871
iteration 2
whale: 2
9872
iteration 2
whale: 2
9873
iteration 2
whale: 2
9874
iteration 2
whale: 2
9875
iteration 2
whale: 2
9876
iteration 2
whale: 2
9877
iteration 2
whale: 2
9878
iteration 2
whale: 2
9879
iteration 2
whale: 2
9880
iteration 2
whale: 2
9881
iteration 2
whale: 2
9882
iteration 2
whale: 2
9883
iteration 2
whale: 2
9884
iteration 2
whale: 2
9885
iteration 2
whale: 2
9886
iteration 2
whale: 2
9887
iteration 2
whale: 2
9888
iteration 2
whale: 2
9889
iteration 2
whale: 2
9890
iteration 2
whale: 2
9891
iteration 2
whale: 2
9892
iteration 2
whale: 2
9893
iteration 2
whale: 2
9894
iteration 2


In [ ]:
bestWhale

In [19]:
#CNN
whale=bestWhale
yPred=np.zeros((dataPoints))
for iteration in range(1):
    print("iteration "+str(iteration))
    for whale1 in range(1):
        error=0.00
        for dataPoint in range(10000):
            #initializations
            print(iteration)
            print(dataPoint)
            #startTime=time.time()
            I1=np.zeros((features))
            sigmaF1=np.zeros((100))
            sigmaC1=np.zeros((5,8,8))
            sigmaC2=np.zeros((6,6))
            sigmaF2=np.zeros((84))
            sigmaF3=np.zeros((10))
            
            I1=X[dataPoint]
            
            #Forward passs at I1
            for nodeI1 in range(features):
                for nodeF1 in range(100):
                    sigmaF1[nodeF1]+=WFC1[whale][nodeI1][nodeF1]*I1[nodeI1]
            
            F1=sigmaF1
            for nodeF1 in range(100):
                if sigmaF1[nodeF1]<0:
                    F1[nodeF1]*=0.05
            sigmaF1=sigmaF1.reshape((10,10))
            F1=F1.reshape((10,10))
            #Forward Pass at I1 done
            
            #Forward pass at F1
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                sigmaC1[kernel][rowC1][colC1]+=WC1[whale][kernel][rowKernel][colKernel]*F1[rowC1+rowKernel][colC1+colKernel]
            
            C1=sigmaC1
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        if C1[kernel][rowC1][colC1]<0:
                            C1[kernel][rowC1][colC1]*=0.05
            #Forward pass at F1 done
            
            #Forward pass at C1
            for rowC2 in range(6):
                for colC2 in range(6):
                    for depthKernel in range(5):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                sigmaC2[rowC2][colC2]+=WC2[whale][depthKernel][rowKernel][colKernel]*C1[depthKernel][rowKernel+rowC2][colKernel+colC2]
            
            C2=sigmaC2
            for rowC2 in range(6):
                for colC2 in range(6):
                    if sigmaC2[rowC2][colC2]<0:
                        C2[rowC2][colC2]*=0.05
            
            sigmaC2=sigmaC2.reshape((36,1))
            C2=C2.reshape((36,1))
            #Forward pass at C1 done
            
            #Forward pass at C2
            for nodeC2 in range(36):
                for nodeF2 in range(84):
                    sigmaF2[nodeF2]+=WFC2[whale][nodeC2][nodeF2]*C2[nodeC2]
            
            F2=sigmaF2
            for nodeF2 in range(84):
                if F2[nodeF2]<0:
                    F2[nodeF2]*=0.05
            #Forward pass at C2 done
            
            #Forward pass at F2
            for nodeF2 in range(84):
                for nodeF3 in range(10):
                    sigmaF3[nodeF3]+=WFC3[whale][nodeF2][nodeF3]*F2[nodeF3]
                    
            F3=sigmaF3
            for nodeF3 in range(10):
                if F3[nodeF3]<0:
                    F3[nodeF3]*=0.05
            #Forward pass at F2 done
            
            #Forward pass at F3
            sum=0.00
            for node in range(10):
                sum+=F3[node]*WOP[whale][node]
            
            op=sum
            yPred[dataPoint]=op
            
            #backpropogation at output
            delOp=op-y[dataPoint]
            delSigmaOp=delOp
            #backpropogation at output done
            
            #backpropogation at F3
            delWOP=delSigmaOp*F3
            delF3=delSigmaOp*WOP[whale]
            delSigmaF3=delF3
            for node in range(10):
                if F3[node]<0:
                    delSigmaF3[node]*=0.005
            #backpropogation at F3 done
            
            #backpropogation at F2
            delWFC3=np.zeros((84,10))
            delF2=np.zeros((84))
            for nodeF2 in range(84):
                for nodeF3 in range(10):
                    delWFC3[nodeF2][nodeF3]+=delSigmaF3[nodeF3]*F2[nodeF2]
                    delF2[nodeF2]+=delSigmaF3[nodeF3]*WFC3[whale][nodeF2][nodeF3]
            
            delSigmaF2=delF2
            for nodeF2 in range(84):
                if F2[nodeF2]<0:
                    delSigmaF2[nodeF2]*=0.05
            #bakpropogation at F2 done
            
            #backpropogation at C2
            delWFC2=np.zeros((36,84))
            delSigmaC2=np.zeros((36))
            for nodeC2 in range(36):
                for nodeF2 in range(84):
                    delWFC2[nodeC2][nodeF2]+=delSigmaF2[nodeF2]*C2[nodeC2]
                    delSigmaC2[nodeC2]+=delSigmaF2[nodeF2]*WFC2[whale][nodeC2][nodeF2]
            
            delC2=delSigmaC2
            for nodeC2 in range(36):
                if C2[nodeC2]<0:
                    delC2[nodeC2]*=0.05
            
            delSigmaC2=delSigmaC2.reshape((6,6))
            delC2=delC2.reshape((6,6))
            #backpropogation at C2
            
            #backpropogation at C1
            delWC2=np.zeros((5,3,3))
            delC1=np.zeros((5,8,8))
            for rowC2 in range(6):
                for colC2 in range(6):
                    for depthKernel in range(5):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                delWC2[depthKernel][rowKernel][colKernel]+=delSigmaC2[rowC2][colC2]*C1[depthKernel][rowKernel+rowC2][colKernel+colC2]
                                delC1[depthKernel][rowKernel+rowC2][colKernel+colC2]+=delSigmaC2[rowC2][colC2]*WC2[whale][depthKernel][rowKernel][colKernel]
            
            delSigmaC1=delC1
            for depthC1 in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        if C1[depthC1][rowC1][colC1]<0:
                            delSigmaC1[depthC1][rowC1][colC1]*=0.05
            
            #backpropogation at C1 done
            
            #backpropgation at F1:
            delWC1=np.zeros((5,3,3))
            delF1=np.zeros((10,10))
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                delWC1[kernel][rowKernel][colKernel]+=delSigmaC1[kernel][rowC1][colC1]*F1[rowC1+rowKernel][colC1+colKernel]
                                delF1[rowC1+rowKernel][colC1+colKernel]+=delSigmaC1[kernel][rowC1][colC1]*WC1[whale][kernel][rowKernel][colKernel]
            
            delSigmaF1=delF1
            for rowF1 in range(10):
                for colF1 in range(10):
                    if F1[rowF1][colF1]<0:
                        delSigmaF1[rowF1][colF1]*=0.05
            
            delSigmaF1=delSigmaF1.reshape((100,1))
            delF1=delF1.reshape((100,1))
            #backpropogation at F1 done
            
            #backpropogation at I1:
            delWFC1=np.zeros((features,100))
            for nodeI1 in range(features):
                for nodeF1 in range(100):
                    delWFC1[nodeI1][nodeF1]+=delF1[nodeF1]*I1[nodeI1]
                            
            #backpropogation at I1 done
            
            #gradient descent:
            for nodeI1 in range(features):
                for nodeF1 in range(100):
                    WFC1[whale][nodeI1][nodeF1]-=learningRate*delWFC1[nodeI1][nodeF1]
            
            for kernel in range(5):
                for rowKernel in range(3):
                    for colKernel in range(3):
                        WC1[whale][kernel][rowKernel][colKernel]-=learningRate*delWC1[kernel][rowKernel][colKernel]
                        
            for depthKernel in range(5):
                for rowKernel in range(3):
                    for colKernel in range(3):
                        WC2[whale][depthKernel][rowKernel][colKernel]-=learningRate*delWC2[depthKernel][rowKernel][colKernel]
            
            for nodeC2 in range(36):
                for nodeF2 in range(84):
                    WFC2[whale][nodeC2][nodeF2]-=learningRate*delWFC2[nodeC2][nodeF2]
            
            for nodeF2 in range(84):
                for nodeF3 in range(10):
                   WFC3[whale][nodeF2][nodeF3]-=learningRate*delWFC3[nodeF2][nodeF3]
            
            for node in range(10):
                WOP[whale][node]-=learningRate*delWOP[node]

iteration 0
0
0
0
1
0
2
0
3
0
4
0
5


/usr/lib/python3/dist-packages/ipykernel_launcher.py:41: RuntimeWarning: overflow encountered in double_scalars
/usr/lib/python3/dist-packages/ipykernel_launcher.py:189: RuntimeWarning: invalid value encountered in multiply
/usr/lib/python3/dist-packages/ipykernel_launcher.py:25: RuntimeWarning: invalid value encountered in double_scalars


0
6
0
7
0
8
0
9
0
10
0
11
0
12
0
13
0
14
0
15
0
16
0
17
0
18
0
19
0
20
0
21
0
22
0
23
0
24
0
25
0
26
0
27
0
28
0
29
0
30
0
31
0
32
0
33
0
34
0
35
0
36
0
37
0
38
0
39
0
40
0
41
0
42
0
43
0
44
0
45
0
46
0
47
0
48
0
49
0
50
0
51
0
52
0
53
0
54
0
55
0
56
0
57
0
58
0
59
0
60
0
61
0
62
0
63
0
64
0
65
0
66
0
67
0
68
0
69
0
70
0
71
0
72
0
73
0
74
0
75
0
76
0
77
0
78
0
79
0
80
0
81
0
82
0
83
0
84
0
85
0
86
0
87
0
88
0
89
0
90
0
91
0
92
0
93
0
94
0
95
0
96
0
97
0
98
0
99
0
100
0
101
0
102
0
103
0
104
0
105
0
106
0
107
0
108
0
109
0
110
0
111
0
112
0
113
0
114
0
115
0
116
0
117
0
118
0
119
0
120
0
121
0
122
0
123
0
124
0
125
0
126
0
127
0
128
0
129
0
130
0
131
0
132
0
133
0
134
0
135
0
136
0
137
0
138
0
139
0
140
0
141
0
142
0
143
0
144
0
145
0
146
0
147
0
148
0
149
0
150
0
151
0
152
0
153
0
154
0
155
0
156
0
157
0
158
0
159
0
160
0
161
0
162
0
163
0
164
0
165
0
166
0
167
0
168
0
169
0
170
0
171
0
172
0
173
0
174
0
175
0
176
0
177
0
178
0
179
0
180
0
181
0
182
0
183
0
184
0
185
0
186
0
187
0
188


0
1334
0
1335
0
1336
0
1337
0
1338
0
1339
0
1340
0
1341
0
1342
0
1343
0
1344
0
1345
0
1346
0
1347
0
1348
0
1349
0
1350
0
1351
0
1352
0
1353
0
1354
0
1355
0
1356
0
1357
0
1358
0
1359
0
1360
0
1361
0
1362
0
1363
0
1364
0
1365
0
1366
0
1367
0
1368
0
1369
0
1370
0
1371
0
1372
0
1373
0
1374
0
1375
0
1376
0
1377
0
1378
0
1379
0
1380
0
1381
0
1382
0
1383
0
1384
0
1385
0
1386
0
1387
0
1388
0
1389
0
1390
0
1391
0
1392
0
1393
0
1394
0
1395
0
1396
0
1397
0
1398
0
1399
0
1400
0
1401
0
1402
0
1403
0
1404
0
1405
0
1406
0
1407
0
1408
0
1409
0
1410
0
1411
0
1412
0
1413
0
1414
0
1415
0
1416
0
1417
0
1418
0
1419
0
1420
0
1421
0
1422
0
1423
0
1424
0
1425
0
1426
0
1427
0
1428
0
1429
0
1430
0
1431
0
1432
0
1433
0
1434
0
1435
0
1436
0
1437
0
1438
0
1439
0
1440
0
1441
0
1442
0
1443
0
1444
0
1445
0
1446
0
1447
0
1448
0
1449
0
1450
0
1451
0
1452
0
1453
0
1454
0
1455
0
1456
0
1457
0
1458
0
1459
0
1460
0
1461
0
1462
0
1463
0
1464
0
1465
0
1466
0
1467
0
1468
0
1469
0
1470
0
1471
0
1472
0
1473
0
1474
0
1475
0
1476

0
2507
0
2508
0
2509
0
2510
0
2511
0
2512
0
2513
0
2514
0
2515
0
2516
0
2517
0
2518
0
2519
0
2520
0
2521
0
2522
0
2523
0
2524
0
2525
0
2526
0
2527
0
2528
0
2529
0
2530
0
2531
0
2532
0
2533
0
2534
0
2535
0
2536
0
2537
0
2538
0
2539
0
2540
0
2541
0
2542
0
2543
0
2544
0
2545
0
2546
0
2547
0
2548
0
2549
0
2550
0
2551
0
2552
0
2553
0
2554
0
2555
0
2556
0
2557
0
2558
0
2559
0
2560
0
2561
0
2562
0
2563
0
2564
0
2565
0
2566
0
2567
0
2568
0
2569
0
2570
0
2571
0
2572
0
2573
0
2574
0
2575
0
2576
0
2577
0
2578
0
2579
0
2580
0
2581
0
2582
0
2583
0
2584
0
2585
0
2586
0
2587
0
2588
0
2589
0
2590
0
2591
0
2592
0
2593
0
2594
0
2595
0
2596
0
2597
0
2598
0
2599
0
2600
0
2601
0
2602
0
2603
0
2604
0
2605
0
2606
0
2607
0
2608
0
2609
0
2610
0
2611
0
2612
0
2613
0
2614
0
2615
0
2616
0
2617
0
2618
0
2619
0
2620
0
2621
0
2622
0
2623
0
2624
0
2625
0
2626
0
2627
0
2628
0
2629
0
2630
0
2631
0
2632
0
2633
0
2634
0
2635
0
2636
0
2637
0
2638
0
2639
0
2640
0
2641
0
2642
0
2643
0
2644
0
2645
0
2646
0
2647
0
2648
0
2649

...

0
4851
0
4852
0
4853
0
4854
0
4855
0
4856
0
4857
0
4858
0
4859
0
4860
0
4861
0
4862
0
4863
0
4864
0
4865
0
4866
0
4867
0
4868
0
4869
0
4870
0
4871
0
4872
0
4873
0
4874
0
4875
0
4876
0
4877
0
4878
0
4879
0
4880
0
4881
0
4882
0
4883
0
4884
0
4885
0
4886
0
4887
0
4888
0
4889
0
4890
0
4891
0
4892
0
4893
0
4894
0
4895
0
4896
0
4897
0
4898
0
4899
0
4900
0
4901
0
4902
0
4903
0
4904
0
4905
0
4906
0
4907
0
4908
0
4909
0
4910
0
4911
0
4912
0
4913
0
4914
0
4915
0
4916
0
4917
0
4918
0
4919
0
4920
0
4921
0
4922
0
4923
0
4924
0
4925
0
4926
0
4927
0
4928
0
4929
0
4930
0
4931
0
4932
0
4933
0
4934
0
4935
0
4936
0
4937
0
4938
0
4939
0
4940
0
4941
0
4942
0
4943
0
4944
0
4945
0
4946
0
4947
0
4948
0
4949
0
4950
0
4951
0
4952
0
4953
0
4954
0
4955
0
4956
0
4957
0
4958
0
4959
0
4960
0
4961
0
4962
0
4963
0
4964
0
4965
0
4966
0
4967
0
4968
0
4969
0
4970
0
4971
0
4972
0
4973
0
4974
0
4975
0
4976
0
4977
0
4978
0
4979
0
4980
0
4981
0
4982
0
4983
0
4984
0
4985
0
4986
0
4987
0
4988
0
4989
0
4990
0
4991
0
4992
0
4993

0
6025
0
6026
0
6027
0
6028
0
6029
0
6030
0
6031
0
6032
0
6033
0
6034
0
6035
0
6036
0
6037
0
6038
0
6039
0
6040
0
6041
0
6042
0
6043
0
6044
0
6045
0
6046
0
6047
0
6048
0
6049
0
6050
0
6051
0
6052
0
6053
0
6054
0
6055
0
6056
0
6057
0
6058
0
6059
0
6060
0
6061
0
6062
0
6063
0
6064
0
6065
0
6066
0
6067
0
6068
0
6069
0
6070
0
6071
0
6072
0
6073
0
6074
0
6075
0
6076
0
6077
0
6078
0
6079
0
6080
0
6081
0
6082
0
6083
0
6084
0
6085
0
6086
0
6087
0
6088
0
6089
0
6090
0
6091
0
6092
0
6093
0
6094
0
6095
0
6096
0
6097
0
6098
0
6099
0
6100
0
6101
0
6102
0
6103
0
6104
0
6105
0
6106
0
6107
0
6108
0
6109
0
6110
0
6111
0
6112
0
6113
0
6114
0
6115
0
6116
0
6117
0
6118
0
6119
0
6120
0
6121
0
6122
0
6123
0
6124
0
6125
0
6126
0
6127
0
6128
0
6129
0
6130
0
6131
0
6132
0
6133
0
6134
0
6135
0
6136
0
6137
0
6138
0
6139
0
6140
0
6141
0
6142
0
6143
0
6144
0
6145
0
6146
0
6147
0
6148
0
6149
0
6150
0
6151
0
6152
0
6153
0
6154
0
6155
0
6156
0
6157
0
6158
0
6159
0
6160
0
6161
0
6162
0
6163
0
6164
0
6165
0
6166
0
6167

0
7197
0
7198
0
7199
0
7200
0
7201
0
7202
0
7203
0
7204
0
7205
0
7206
0
7207
0
7208
0
7209
0
7210
0
7211
0
7212
0
7213
0
7214
0
7215
0
7216
0
7217
0
7218
0
7219
0
7220
0
7221
0
7222
0
7223
0
7224
0
7225
0
7226
0
7227
0
7228
0
7229
0
7230
0
7231
0
7232
0
7233
0
7234
0
7235
0
7236
0
7237
0
7238
0
7239
0
7240
0
7241
0
7242
0
7243
0
7244
0
7245
0
7246
0
7247
0
7248
0
7249
0
7250
0
7251
0
7252
0
7253
0
7254
0
7255
0
7256
0
7257
0
7258
0
7259
0
7260
0
7261
0
7262
0
7263
0
7264
0
7265
0
7266
0
7267
0
7268
0
7269
0
7270
0
7271
0
7272
0
7273
0
7274
0
7275
0
7276
0
7277
0
7278
0
7279
0
7280
0
7281
0
7282
0
7283
0
7284
0
7285
0
7286
0
7287
0
7288
0
7289
0
7290
0
7291
0
7292
0
7293
0
7294
0
7295
0
7296
0
7297
0
7298
0
7299
0
7300
0
7301
0
7302
0
7303
0
7304
0
7305
0
7306
0
7307
0
7308
0
7309
0
7310
0
7311
0
7312
0
7313
0
7314
0
7315
0
7316
0
7317
0
7318
0
7319
0
7320
0
7321
0
7322
0
7323
0
7324
0
7325
0
7326
0
7327
0
7328
0
7329
0
7330
0
7331
0
7332
0
7333
0
7334
0
7335
0
7336
0
7337
0
7338
0
7339

0
8368
0
8369
0
8370
0
8371
0
8372
0
8373
0
8374
0
8375
0
8376
0
8377
0
8378
0
8379
0
8380
0
8381
0
8382
0
8383
0
8384
0
8385
0
8386
0
8387
0
8388
0
8389
0
8390
0
8391
0
8392
0
8393
0
8394
0
8395
0
8396
0
8397
0
8398
0
8399
0
8400
0
8401
0
8402
0
8403
0
8404
0
8405
0
8406
0
8407
0
8408
0
8409
0
8410
0
8411
0
8412
0
8413
0
8414
0
8415
0
8416
0
8417
0
8418
0
8419
0
8420
0
8421
0
8422
0
8423
0
8424
0
8425
0
8426
0
8427
0
8428
0
8429
0
8430
0
8431
0
8432
0
8433
0
8434
0
8435
0
8436
0
8437
0
8438
0
8439
0
8440
0
8441
0
8442
0
8443
0
8444
0
8445
0
8446
0
8447
0
8448
0
8449
0
8450
0
8451
0
8452
0
8453
0
8454
0
8455
0
8456
0
8457
0
8458
0
8459
0
8460
0
8461
0
8462
0
8463
0
8464
0
8465
0
8466
0
8467
0
8468
0
8469
0
8470
0
8471
0
8472
0
8473
0
8474
0
8475
0
8476
0
8477
0
8478
0
8479
0
8480
0
8481
0
8482
0
8483
0
8484
0
8485
0
8486
0
8487
0
8488
0
8489
0
8490
0
8491
0
8492
0
8493
0
8494
0
8495
0
8496
0
8497
0
8498
0
8499
0
8500
0
8501
0
8502
0
8503
0
8504
0
8505
0
8506
0
8507
0
8508
0
8509
0
8510

0
9542
0
9543
0
9544
0
9545
0
9546
0
9547
0
9548
0
9549
0
9550
0
9551
0
9552
0
9553
0
9554
0
9555
0
9556
0
9557
0
9558
0
9559
0
9560
0
9561
0
9562
0
9563
0
9564
0
9565
0
9566
0
9567
0
9568
0
9569
0
9570
0
9571
0
9572
0
9573
0
9574
0
9575
0
9576
0
9577
0
9578
0
9579
0
9580
0
9581
0
9582
0
9583
0
9584
0
9585
0
9586
0
9587
0
9588
0
9589
0
9590
0
9591
0
9592
0
9593
0
9594
0
9595
0
9596
0
9597
0
9598
0
9599
0
9600
0
9601
0
9602
0
9603
0
9604
0
9605
0
9606
0
9607
0
9608
0
9609
0
9610
0
9611
0
9612
0
9613
0
9614
0
9615
0
9616
0
9617
0
9618
0
9619
0
9620
0
9621
0
9622
0
9623
0
9624
0
9625
0
9626
0
9627
0
9628
0
9629
0
9630
0
9631
0
9632
0
9633
0
9634
0
9635
0
9636
0
9637
0
9638
0
9639
0
9640
0
9641
0
9642
0
9643
0
9644
0
9645
0
9646
0
9647
0
9648
0
9649
0
9650
0
9651
0
9652
0
9653
0
9654
0
9655
0
9656
0
9657
0
9658
0
9659
0
9660
0
9661
0
9662
0
9663
0
9664
0
9665
0
9666
0
9667
0
9668
0
9669
0
9670
0
9671
0
9672
0
9673
0
9674
0
9675
0
9676
0
9677
0
9678
0
9679
0
9680
0
9681
0
9682
0
9683
0
9684

In [20]:
X=np.zeros((943*1682,23))
for user in range(943):
    print(user)
    for movie in range(1682):
        i=0
        for userInfo in range(4):
            X[user][i]=XUser[user][userInfo]
            i=i+1
        for movieInfo in range(19):
            X[user][i]=XItem[movie][movieInfo]
            i=i+1

dataPoints=943*1682

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [22]:
#For result
dataPoints=943
yPred=np.zeros((943,1682))
for iteration in range(1):
    print("iteration "+str(iteration))
    for whale1 in range(1):
        error=0.00
        for dataPoint in range(dataPoints):
            #initializations
            print(dataPoint)
            #startTime=time.time()
            I1=np.zeros((features))
            sigmaF1=np.zeros((100))
            sigmaC1=np.zeros((5,8,8))
            sigmaC2=np.zeros((6,6))
            sigmaF2=np.zeros((84))
            sigmaF3=np.zeros((10))
            
            I1=X[dataPoint]
            
            #Forward passs at I1
            for nodeI1 in range(features):
                for nodeF1 in range(100):
                    sigmaF1[nodeF1]+=WFC1[whale][nodeI1][nodeF1]*I1[nodeI1]
            
            F1=sigmaF1
            for nodeF1 in range(100):
                if sigmaF1[nodeF1]<0:
                    F1[nodeF1]*=0.05
            sigmaF1=sigmaF1.reshape((10,10))
            F1=F1.reshape((10,10))
            #Forward Pass at I1 done
            
            #Forward pass at F1
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                sigmaC1[kernel][rowC1][colC1]+=WC1[whale][kernel][rowKernel][colKernel]*F1[rowC1+rowKernel][colC1+colKernel]
            
            C1=sigmaC1
            for kernel in range(5):
                for rowC1 in range(8):
                    for colC1 in range(8):
                        if C1[kernel][rowC1][colC1]<0:
                            C1[kernel][rowC1][colC1]*=0.05
            #Forward pass at F1 done
            
            #Forward pass at C1
            for rowC2 in range(6):
                for colC2 in range(6):
                    for depthKernel in range(5):
                        for rowKernel in range(3):
                            for colKernel in range(3):
                                sigmaC2[rowC2][colC2]+=WC2[whale][depthKernel][rowKernel][colKernel]*C1[depthKernel][rowKernel+rowC2][colKernel+colC2]
            
            C2=sigmaC2
            for rowC2 in range(6):
                for colC2 in range(6):
                    if sigmaC2[rowC2][colC2]<0:
                        C2[rowC2][colC2]*=0.05
            
            sigmaC2=sigmaC2.reshape((36,1))
            C2=C2.reshape((36,1))
            #Forward pass at C1 done
            
            #Forward pass at C2
            for nodeC2 in range(36):
                for nodeF2 in range(84):
                    sigmaF2[nodeF2]+=WFC2[whale][nodeC2][nodeF2]*C2[nodeC2]
            
            F2=sigmaF2
            for nodeF2 in range(84):
                if F2[nodeF2]<0:
                    F2[nodeF2]*=0.05
            #Forward pass at C2 done
            
            #Forward pass at F2
            for nodeF2 in range(84):
                for nodeF3 in range(10):
                    sigmaF3[nodeF3]+=WFC3[whale][nodeF2][nodeF3]*F2[nodeF3]
                    
            F3=sigmaF3
            for nodeF3 in range(10):
                if F3[nodeF3]<0:
                    F3[nodeF3]*=0.05
            #Forward pass at F2 done
            
            #Forward pass at F3
            sum=0.00
            for node in range(10):
                sum+=F3[node]*WOP[whale][node]
            
            op=sum
            yPred[dataPoint]=op


iteration 0
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
27

In [23]:
yPred=yPred.reshape(943,1682)


In [24]:
yPred

array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       ...,
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan]])

In [ ]:
j=5
while j<=20:
    precision=0.00
    for dataPoint in range(943):
        arr1=recommendMatrix[dataPoint].argsort()[-j:][::-1]
        arr2=yPred[dataPoint].argsort()[-j:][::-1]    
        intersection=np.intersect1d(arr1,arr2)
        precision+=(intersection.shape[0])/50
    precision/=943
    print(precision)
    j+=5

